# Visualize HARP2 CLOUD GPC Product

**Authors:** Chamara (NASA, SSAI), Kirk (NASA), Andy (NASA, UMBC), Meng (NASA, SSAI), Sean (NASA, MSU)

[edl]: https://urs.earthdata.nasa.gov/
[oci-data-access]: https://oceancolor.gsfc.nasa.gov/resources/docs/tutorials/notebooks/oci_data_access/

## Summary
This notebook summarizes how to access HARP2 GISS Polarimetric Cloud (GPC) products (CLOUD_GPC.V3_0).
Note that this notebook is based on an early preliminary version of the product and is therefore subject to future optimizations and changes.

## Learning Objectives
By the end of this notebook, you will understand:

- How to acquire HARP2 L2 data
- Available variables in the product
- How to visualize variables

## Contents

1. [Setup](#1.-Setup)
2. [Get Level-2 Data](#2.-Get-Level-2-Data)
3. [Understanding HARP2 L2 product structure](#3.-Understanding-HARP2-L2.CLOUD_GPC-Product-Structure)
4. [4. Visulizing Variables](#4.-Visulizing-Variables)
5. [Reference](#5.-Reference)

## 1. Setup

Begin by importing all of the packages used in this notebook. If your kernel uses an environment defined following the guidance on the [tutorials] page, then the imports will be successful.

[tutorials]: https://oceancolor.gsfc.nasa.gov/resources/docs/tutorials/

In [ ]:
from pathlib import Path
from textwrap import wrap

import cartopy.crs as ccrs
import earthaccess
import matplotlib.colors as mcolors
import matplotlib.pyplot as plt
import numpy as np
import requests
import xarray as xr

plt.style.use("seaborn-v0_8-notebook")

In [ ]:
auth = earthaccess.login(persist=True)
fs = earthaccess.get_fsspec_https_session()

[back to top](#Contents)

## 2. Get Level-2 Data

HARP2 L2.CLOUD_GPC_NRT products are currently available starting from 2025-07-01. You can use the following "short name" to search with earthaccess.search_data:

In [ ]:
results = earthaccess.search_datasets(instrument="harp2")
for item in results:
    summary = item.summary()
    print(summary["short-name"])

In [ ]:
results = earthaccess.search_data(
    short_name="PACE_HARP2_L2_CLOUD_GPC_NRT",
    temporal=("2025-07-02", "2025-07-02"),
    bounding_box=(-90, -15, -89, -14),  # (west, south, east, north) if desired
    count=1,
)
paths = earthaccess.open(results)

In [ ]:
paths

In [ ]:
datatree = xr.open_datatree(paths[0])
# datatree

Here we merge all the data group together for convenience in data manipulations.

In [ ]:
dataset = xr.merge(datatree.to_dict().values())
# dataset

[back to top](#Contents)

## 3. Understanding HARP2 L2.CLOUD_GPC Product Structure

HARP2 CLOUD_GPC products provide descriptive metadata for the variables. However, given the early stage of the product, improvements and changes are expected in future versions.

In [ ]:
def print_variable_description(datatree, ret_type_list, exclude=False):
    """
    To print variables and descriptions in a table
    """
    print(f"{'Variable':50} | {'Units':10} | Description")
    print("-" * 100)

    for var, da in datatree["geophysical_data"].items():
        # Check inclusion/exclusion logic
        match = any(key in var for key in ret_type_list)
        if (match and not exclude) or (not match and exclude):
            units = da.attrs.get("units", "")
            desc = da.attrs.get("long_name", "")
            wrapped = wrap(desc, 100)
            print(f"{var:50} | {units:10} | {wrapped[0]}")
            for line in wrapped[1:]:
                print(f"{'':50} | {'':10} | {line}")

### Cloud Bow Retrievals
One of the main retrieval techniques implemented is the parametric cloud bow retrieval method (Bréon & Goloub, 1998; Alexandrov et al., 2012). The phrase "cloud_bow" is appended to variable names, their corresponding diagnostic variables, and additional variables derived by combining them with OCI Level 2 products. For example, "cloud_bow_droplet_number_concentration_adiabatic" and "cloud_bow_liquid_water_path" are derived using the retrieved droplet size distributions along with OCI L2.CLOUD properties.

In [ ]:
print_variable_description(datatree, ["bow"])

### RFT Retrievals
The second retrieval technique is the Rainbow Fourier Transform (RFT) method (Alexandrov et al., 2012). The prefix cloud_rft is appended to variable names, their associated diagnostic variables, and other outputs generated by this algorithm.

In [ ]:
print_variable_description(datatree, ["rft"])

### Cloud Liquid Index Retrievals

In [ ]:
print_variable_description(datatree, ["index"], exclude=False)

### Additional Variables From OCI L2.CLOUD Products

In [ ]:
print_variable_description(datatree, ["index", "rft", "bow"], exclude=True)

[back to top](#Contents)

## 4. Visulizing Variables

In [ ]:
transform = ccrs.PlateCarree(central_longitude=0)
projection = ccrs.PlateCarree()


def extremes_removed_ids(x):
    """
    Returns indices of array x after removing the extreme values
    """
    q3 = np.percentile(x, 75)
    q1 = np.percentile(x, 25)
    xmin = q1 - 1.5 * (q3 - q1)
    xmax = q3 + 1.5 * (q3 - q1)
    return (xmin <= x) * (x < xmax)


def geo_axis_tags(ax, crs=ccrs.PlateCarree(central_longitude=0)):
    gl = ax.gridlines(crs=crs, draw_labels=True)
    ax.coastlines()
    # gl = ax.gridlines(draw_labels=True,linestyle='--',\
    #     xlocs=mticker.FixedLocator(np.arange(-180,180.1,10)),ylocs=mticker.FixedLocator(np.arange(-90,90.1,10)))
    gl.top_labels = False
    gl.right_labels = False
    gl.xlabel_style = {"size": 12, "color": "k"}
    gl.ylabel_style = {"size": 12, "color": "k"}

    ax.coastlines()
    return gl

In [ ]:
var = "cloud_bow_droplet_effective_radius"
fig1, ax1 = plt.subplots(figsize=(10, 6), subplot_kw={"projection": projection})
cmap = plt.get_cmap("viridis", 20)
_arr = dataset[var].values
arr_tes = np.ma.masked_array(_arr, mask=np.isnan(_arr))
# vmin, vmax = har_l2_tes.read_from_file('retrievals/%s'%variable_list[i],attrs_local='valid_min'), har_l2_tes.read_from_file('retrievals/%s'%variable_list[i],attrs_local='valid_max')
vmin, vmax = (
    arr_tes.compressed()[extremes_removed_ids(arr_tes.compressed())].min(),
    arr_tes.compressed()[extremes_removed_ids(arr_tes.compressed())].max(),
)
ctf = ax1.pcolormesh(
    dataset.longitude,
    dataset.latitude,
    arr_tes,
    transform=transform,
    cmap=cmap,
    vmin=vmin,
    vmax=vmax,
)
ax1.set_title(var, size=12)
gl = geo_axis_tags(ax1, crs=transform)
# plt.colorbar(pm, ax=ax_map, orientation="vertical", pad=0.1, label=label)
fig1.colorbar(
    ctf, ax=ax1, orientation="vertical", label="%s [%s]" % (var, dataset[var].units)
)

In [ ]:
var = "cloud_bow_droplet_effective_variance"
fig1, ax1 = plt.subplots(figsize=(10, 6), subplot_kw={"projection": projection})
cmap = plt.get_cmap("viridis", 40)
norm = mcolors.LogNorm(vmin=0.005, vmax=0.4)
_arr = dataset[var].values
arr_tes = np.ma.masked_array(_arr, mask=np.isnan(_arr))
# vmin, vmax = arr_tes.compressed()[extremes_removed_ids(arr_tes.compressed())].min(), arr_tes.compressed()[extremes_removed_ids(arr_tes.compressed())].max()
ctf = ax1.pcolormesh(
    dataset.longitude,
    dataset.latitude,
    arr_tes,
    transform=transform,
    cmap=cmap,
    norm=norm,
)
ax1.set_title(var, size=12)
gl = geo_axis_tags(ax1, crs=transform)
# plt.colorbar(pm, ax=ax_map, orientation="vertical", pad=0.1, label=label)
fig1.colorbar(
    ctf, ax=ax1, orientation="vertical", label="%s [%s]" % (var, dataset[var].units)
)

In [ ]:
var = "cloud_bow_liquid_water_path"
fig1, ax1 = plt.subplots(figsize=(10, 6), subplot_kw={"projection": projection})
cmap = plt.get_cmap("viridis", 20)
_arr = dataset[var].values
arr_tes = np.ma.masked_array(_arr, mask=np.isnan(_arr))
# vmin, vmax = har_l2_tes.read_from_file('retrievals/%s'%variable_list[i],attrs_local='valid_min'), har_l2_tes.read_from_file('retrievals/%s'%variable_list[i],attrs_local='valid_max')
vmin, vmax = (
    arr_tes.compressed()[extremes_removed_ids(arr_tes.compressed())].min(),
    arr_tes.compressed()[extremes_removed_ids(arr_tes.compressed())].max(),
)
ctf = ax1.pcolormesh(
    dataset.longitude,
    dataset.latitude,
    arr_tes,
    transform=transform,
    cmap=cmap,
    vmin=vmin,
    vmax=vmax,
)
ax1.set_title(var, size=12)
gl = geo_axis_tags(ax1, crs=transform)
# plt.colorbar(pm, ax=ax_map, orientation="vertical", pad=0.1, label=label)
fig1.colorbar(
    ctf, ax=ax1, orientation="vertical", label="%s [%s]" % (var, dataset[var].units)
)

[back to top](#Contents)

## 5. Reference

- Breon, F.-M., & Doutriaux-Boucher, M. (2005). A comparison of cloud droplet radii measured from space. IEEE Transactions on Geoscience and Remote Sensing, 43(8), 1796–1805. https://doi.org/10.1109/TGRS.2005.852838
- Alexandrov, M. D., Cairns, B., Emde, C., Ackerman, A. S., & Van Diedenhoven, B. (2012). Accuracy assessments of cloud droplet size retrievals from polarized reflectance measurements by the research scanning polarimeter. Remote Sensing of Environment, 125, 92–111. https://doi.org/10.1016/j.rse.2012.07.012
- Van Diedenhoven, B., Fridlind, A. M., Ackerman, A. S., & Cairns, B. (2012). Evaluation of Hydrometeor Phase and Ice Properties in Cloud-Resolving Model Simulations of Tropical Deep Convection Using Radiance and Polarization Measurements. Journal of the Atmospheric Sciences, 69(11), 3290–3314. https://doi.org/10.1175/JAS-D-11-0314.1
- Alexandrov, M. D., Cairns, B., & Mishchenko, M. I. (2012). Rainbow Fourier transform. Journal of Quantitative Spectroscopy and Radiative Transfer, 113(18), 2521–2535. https://doi.org/10.1016/j.jqsrt.2012.03.025

[back to top](#Contents)